In [1]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline

c:\Users\msk23\flaskenv\flaskenv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Load the dataset
df = pd.read_csv('medquad.csv')

# Display the first few rows of the dataset to understand its structure
print(df.head())


                                 question  \
0                What is (are) Glaucoma ?   
1                  What causes Glaucoma ?   
2     What are the symptoms of Glaucoma ?   
3  What are the treatments for Glaucoma ?   
4                What is (are) Glaucoma ?   

                                              answer  
0  Glaucoma is a group of diseases that can damag...  
1  Nearly 2.7 million people have glaucoma, a lea...  
2  Symptoms of Glaucoma  Glaucoma can develop in ...  
3  Although open-angle glaucoma cannot be cured, ...  
4  Glaucoma is a group of diseases that can damag...  


In [3]:
# Remove unnecessary columns (if any)
df = df.drop(columns=['source'], errors='ignore')  # Adjust based on your dataset

# Handle missing values
df = df.dropna(subset=['question', 'answer'])  # Remove rows where question or answer is missing


In [4]:
# Normalize text
df['question'] = df['question'].str.lower().str.strip()
df['answer'] = df['answer'].str.lower().str.strip()


In [5]:
# Remove punctuation from questions and answers
df['question'] = df['question'].str.replace(r'[^\w\s]', '', regex=True)
df['answer'] = df['answer'].str.replace(r'[^\w\s]', '', regex=True)


In [6]:
# Display the cleaned data
print(df.head())


                                question  \
0                  what is are glaucoma    
1                  what causes glaucoma    
2     what are the symptoms of glaucoma    
3  what are the treatments for glaucoma    
4                  what is are glaucoma    

                                              answer  
0  glaucoma is a group of diseases that can damag...  
1  nearly 27 million people have glaucoma a leadi...  
2  symptoms of glaucoma  glaucoma can develop in ...  
3  although openangle glaucoma cannot be cured it...  
4  glaucoma is a group of diseases that can damag...  


In [7]:
# Load the pre-trained BioBERT model
model_name = "dmis-lab/biobert-v1.1"  # You can change this to another model if needed
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForTokenClassification.from_pretrained(model_name)

Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-v1.1 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [8]:
# Create a NER pipeline
ner_pipeline = pipeline("ner", model=model, tokenizer=tokenizer)


In [9]:
# Function to get answer based on user question
def get_answer(user_question):
    # Perform NER on the user's question
    ner_results = ner_pipeline(user_question)

    # Extract entities from the NER results
    entities = [result['word'] for result in ner_results]

    # Generate a filtered answer based on the identified entities
    answer_candidates = []
    for _, row in df.iterrows():
        # Check if the answer contains any of the extracted entities
        if any(entity in row['answer'] for entity in entities):
            answer_candidates.append(row['answer'])

    # If answer candidates are found, prioritize based on specificity
    if answer_candidates:
        # Select the first relevant answer, focusing on specificity and brevity
        selected_answer = answer_candidates[0]  # You can adjust this logic if needed
    else:
        selected_answer = "Sorry, I couldn't find an answer to your question."

    return selected_answer

In [ ]:
!pip install sentence_transformers

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 255.2/255.2 kB 7.7 MB/s eta 0:00:00


In [ ]:
!pip install faiss-cpu

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.5/27.5 MB 48.7 MB/s eta 0:00:00


In [9]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline, AutoModelForSeq2SeqLM
from sentence_transformers import SentenceTransformer, util
import faiss
import torch
from multiprocessing import Pool

# Load the dataset
df = pd.read_csv('medquad.csv')

# Load models
model_name = "dmis-lab/biobert-v1.1"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForTokenClassification.from_pretrained(model_name)
ner_pipeline = pipeline("ner", model=model, tokenizer=tokenizer)

embedder = SentenceTransformer('all-MiniLM-L6-v2')

# Batch processing of embeddings
batch_size = 64
embeddings = []
for i in range(0, len(df), batch_size):
    batch = df['question'][i:i+batch_size].tolist()
    batch_embeddings = embedder.encode(batch, convert_to_tensor=True, show_progress_bar=True)
    embeddings.append(batch_embeddings)
embedding_matrix = torch.cat(embeddings).cpu().detach().numpy()

# Build FAISS index
d = embedding_matrix.shape[1]
index = faiss.IndexFlatL2(d)
index.add(embedding_matrix)

# Save FAISS index
faiss.write_index(index, "faiss_index.bin")

from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, pipeline





# Function to extract named entities
def extract_entities(text):
    tokens = tokenizer(text, return_tensors="pt", truncation=True, padding=True)
    outputs = model(**tokens)
    predictions = torch.argmax(outputs.logits, dim=2)
    entities = []
    for pred, tok in zip(predictions[0], tokens['input_ids'][0]):
        if pred != 0:
            entities.append(tokenizer.decode([tok]))
    return entities

# Load the summarization model and tokenizer
summarizer_model_name = "facebook/bart-large-cnn"
summarizer_tokenizer = AutoTokenizer.from_pretrained(summarizer_model_name)
summarizer_model = AutoModelForSeq2SeqLM.from_pretrained(summarizer_model_name)
summarization_pipeline = pipeline("summarization", model=summarizer_model, tokenizer=summarizer_tokenizer)

# Function to summarize the answer
def summarize_text(text, max_length=200, min_length=50):
    summary = summarization_pipeline(text, max_length=max_length, min_length=min_length, do_sample=False)
    return summary[0]['summary_text']


# Function to retrieve the best matching answer and summarize it
def get_answer(user_question, df, threshold=0.75):
    # Pre-calculate user question embedding
    user_question_embedding = embedder.encode(user_question, convert_to_tensor=True).cpu().detach().numpy()

    # Search for top 5 closest matches using FAISS
    D, I = index.search(user_question_embedding.reshape(1, -1), 5)

    # Retrieve the best match
    best_match_idx = I[0][0]
    best_match_score = D[0][0]

    # Retrieve answer if similarity score is above threshold
    if best_match_score <= threshold:
        best_answer = df.loc[best_match_idx, 'answer']

        # Extract named entities for further refinement
        answer_entities = extract_entities(best_answer)
        user_entities = extract_entities(user_question)

        # If entities match, return the summarized answer
        if set(user_entities).intersection(set(answer_entities)):
            summarized_answer = summarize_text(best_answer)
            return summarized_answer
        else:
            summarized_answer = summarize_text(best_answer)
            return f"Entities do not match well. Best guess answer: {summarized_answer}"
    else:
        return "Sorry, I couldn't find a relevant answer."

# Example query
user_input = "What causes glaucoma?"
answer = get_answer(user_input, df)
print(f"Answer: {answer}")


/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-v1.1 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


Answer: Nearly 2.7 million people have glaucoma, a leading cause of blindness in the United States. In addition to age, eye pressure is a risk factor. Another risk factor for optic nerve damage relates to blood pressure. It is important to also make sure that your blood pressure is at a proper level.


## ***New Implementation***

In [12]:
!pip install requests


In [25]:
import pandas as pd
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline, AutoModelForSeq2SeqLM
from sentence_transformers import SentenceTransformer, util
import faiss
import torch
import requests  # Import requests for API calls
from multiprocessing import Pool

# Load the dataset
df = pd.read_csv('medquad.csv')

# Load models
model_name = "dmis-lab/biobert-v1.1"
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForTokenClassification.from_pretrained(model_name)
ner_pipeline = pipeline("ner", model=model, tokenizer=tokenizer)

embedder = SentenceTransformer('all-MiniLM-L6-v2')

# Batch processing of embeddings
batch_size = 64
embeddings = []
for i in range(0, len(df), batch_size):
    batch = df['question'][i:i+batch_size].tolist()
    batch_embeddings = embedder.encode(batch, convert_to_tensor=True, show_progress_bar=True)
    embeddings.append(batch_embeddings)
embedding_matrix = torch.cat(embeddings).cpu().detach().numpy()

# Build FAISS index
d = embedding_matrix.shape[1]
index = faiss.IndexFlatL2(d)
index.add(embedding_matrix)

# Save FAISS index
faiss.write_index(index, "faiss_index.bin")

# Function to extract named entities
def extract_entities(text):
    tokens = tokenizer(text, return_tensors="pt", truncation=True, padding=True)
    outputs = model(**tokens)
    predictions = torch.argmax(outputs.logits, dim=2)
    entities = []
    for pred, tok in zip(predictions[0], tokens['input_ids'][0]):
        if pred != 0:
            entities.append(tokenizer.decode([tok]))
    return entities

# Load the summarization model and tokenizer
summarizer_model_name = "facebook/bart-large-cnn"
summarizer_tokenizer = AutoTokenizer.from_pretrained(summarizer_model_name)
summarizer_model = AutoModelForSeq2SeqLM.from_pretrained(summarizer_model_name)
summarization_pipeline = pipeline("summarization", model=summarizer_model, tokenizer=summarizer_tokenizer)

# Function to summarize the answer
def summarize_text(text, max_length=300, min_length=50):
    summary = summarization_pipeline(text, max_length=max_length, min_length=min_length, do_sample=False)
    return summary[0]['summary_text']

# Function to call the MedlinePlus API
def fetch_external_answer(query):
    api_url = f"https://wsearch.nlm.nih.gov/ws/query?db=healthTopics&term={query}&retmode=xml"
    response = requests.get(api_url)
    if response.status_code == 200:
        # Process the response XML or JSON as needed
        # Example: Extract and return relevant information from the API response
        return response.text  # Modify this to extract specific details as required
    else:
        return "API call failed."

# Function to retrieve the best matching answer and summarize it
def get_answer(user_question, df, threshold=0.75):
    # Pre-calculate user question embedding
    user_question_embedding = embedder.encode(user_question, convert_to_tensor=True).cpu().detach().numpy()

    # Search for top 5 closest matches using FAISS
    D, I = index.search(user_question_embedding.reshape(1, -1), 5)

    # Retrieve the best match
    best_match_idx = I[0][0]
    best_match_score = D[0][0]

    # Retrieve answer if similarity score is above threshold
    if best_match_score <= threshold:
        best_answer = df.loc[best_match_idx, 'answer']

        # Extract named entities for further refinement
        answer_entities = extract_entities(best_answer)
        user_entities = extract_entities(user_question)

        # If entities match, return the summarized answer
        if set(user_entities).intersection(set(answer_entities)):
            summarized_answer = summarize_text(best_answer)
            return summarized_answer
        else:
            summarized_answer = summarize_text(best_answer)
            return f"Entities do not match well. Best guess answer: {summarized_answer}"
    else:
        # If the question is outside the dataset, fetch answer from the API
        external_answer = fetch_external_answer(user_question)
        return f"Confidence: Low\nExternal Answer: {external_answer}"

# Example query



/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-v1.1 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


In [29]:
user_input = input("enter ")
answer = get_answer(user_input, df)
print(f"Answer: {answer}")

enter What is (are) Glaucoma ?
Answer: Glaucoma is a group of diseases that can damage the eye's optic nerve. Most of these involve the drainage system within the eye. The most common type is called open-angle glaucomA. There is no cure for the disease, but there are treatments that may save vision.


In [ ]:
import pickle

# Assuming the processed data `data` (the DataFrame with tokenized and cleaned text) is ready to be saved

# Save the processed dataset to a pickle file
with open(r'C:\Users\msk23\OneDrive\Desktop\NIT\NLP\New folder\NLP.pkl', 'wb') as f:
    pickle.dump(data, f)

print("Processed data has been saved to a pickle file.")
